In [ ]:
# !pip install torch==2.7.1+cpu torchvision torchaudio --index-url https://download.pytorch.org/whl/cpu
# !pip install pandas==2.2.3 scikit-learn==1.6.1 evaluate==0.4.3 datasets==3.0.1 matplotlib
# !pip install transformers==4.54.1 accelerate==1.10.1


In [1]:
import pandas as pd
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification, Trainer, TrainingArguments, AutoModel
import csv
import os
import numpy as np
import torch.nn.functional as F

c:\Users\HRMic\OneDrive - ADvTECH Ltd\Documents\VS code\Python_VS\TWITTER\Research\gpuEnv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


#### 2020

In [ ]:
model_path = "model19_UP/OUTPUT_DIR"
tokenizer = AutoTokenizer.from_pretrained(model_path)
model = AutoModelForSequenceClassification.from_pretrained(model_path)
model.to("cuda")
model.eval()  # (Sanh et al., 2019; Nadzmi, 2022; KGP Talkie, 2023; Khan, 2025)

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.2, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): DistilBertSdpaAttention(
            (dropout): Dropout(p=0.2, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.2, inplace=False)


In [4]:
tweets = pd.read_csv("2020_Sample_Ana_Text_Clean.csv")

In [6]:
results = [] 

for i, t in enumerate(tweets["text"], start=1):
    inputs = tokenizer(t, return_tensors="pt", truncation=True, padding=True, max_length=128).to("cuda")
    with torch.no_grad():
        outputs = model(**inputs)
        logits = outputs.logits
        probs = F.softmax(logits, dim=-1)[0].cpu().numpy()
        pred = probs.argmax()

    print(f"Processing line {i}/{len(tweets)}")

    results.append({
        "tweet": t,
        "logits": logits.tolist(),
        "probabilities": probs.tolist(),
        "predicted_label": model.config.id2label[pred]
    })


Processing line 1/224750
Processing line 2/224750
Processing line 3/224750
Processing line 4/224750
Processing line 5/224750
Processing line 6/224750
Processing line 7/224750
Processing line 8/224750
Processing line 9/224750
Processing line 10/224750
Processing line 11/224750
Processing line 12/224750
Processing line 13/224750
Processing line 14/224750
Processing line 15/224750
Processing line 16/224750
Processing line 17/224750
Processing line 18/224750
Processing line 19/224750
Processing line 20/224750
Processing line 21/224750
Processing line 22/224750
Processing line 23/224750
Processing line 24/224750
Processing line 25/224750
Processing line 26/224750
Processing line 27/224750
Processing line 28/224750
Processing line 29/224750
Processing line 30/224750
Processing line 31/224750
Processing line 32/224750
Processing line 33/224750
Processing line 34/224750
Processing line 35/224750
Processing line 36/224750
Processing line 37/224750
Processing line 38/224750
Processing line 39/22

In [7]:
dfResults = pd.DataFrame(results)
dfResults.to_csv("2020_Sample_Ana_Results_model19.csv", index=False)
dfResults[['predicted_label', 'tweet']].to_csv('2020_Classified_model19.csv', index=False)

In [8]:
dfResults.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224750 entries, 0 to 224749
Data columns (total 4 columns):
 #   Column           Non-Null Count   Dtype 
---  ------           --------------   ----- 
 0   tweet            224750 non-null  object
 1   logits           224750 non-null  object
 2   probabilities    224750 non-null  object
 3   predicted_label  224750 non-null  object
dtypes: object(4)
memory usage: 6.9+ MB
